In [65]:
from dotenv import load_dotenv
from typing import Annotated, List, Tuple
from typing_extensions import TypedDict
from langchain.tools import tool, BaseTool
from langchain.schema import Document
from langgraph.graph import StateGraph, START, END, MessagesState
from langgraph.graph.message import add_messages
from langgraph.prebuilt import ToolNode, tools_condition
from langgraph.checkpoint.memory import MemorySaver
from langchain_openai import ChatOpenAI
from langchain_core.prompts import ChatPromptTemplate, SystemMessagePromptTemplate, AIMessagePromptTemplate, HumanMessagePromptTemplate
from langchain.schema import SystemMessage, HumanMessage, AIMessage
from langchain.retrievers.multi_query import MultiQueryRetriever
import gradio as gr

from IPython.display import Image, display
import sys
import os
import uuid


load_dotenv('/Users/nadaa/Documents/code/py_innovations/srf_chatbot_v2/.env')

sys.path.append(os.path.abspath('..'))
%load_ext autoreload
%autoreload 2

import src.utils.qdrant_manager as qm
import prompts.system_prompts as sp





The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [64]:
class ToolManager:
    def __init__(self, collection_name="openai_large_chunks_1500char"):
        self.tools = []
        self.qdrant = qm.QdrantManager(collection_name=collection_name)
        self.vectorstore = self.qdrant.get_vectorstore()
        self.add_vector_search_tool()

    def get_tools(self):
        return self.tools

    def add_vector_search_tool(self):
        @tool
        def vector_search(query: str, k: int = 5) -> list[Document]:
            """Useful for simple queries. This tool will search a vector database for passages from the teachings of Paramhansa Yogananda and other publications from the Self Realization Fellowship (SRF).
            The user has the option to specify the number of passages they want the search to return, otherwise the number of passages will be set to the default value."""
            retriever = self.vectorstore.as_retriever(search_kwargs={"k": k})
            documents = retriever.invoke(query)
            return documents
        
        
        @tool
        def multiple_query_vector_search(query: str, k: int = 5) -> list[Document]:
            """Useful when the user's query is vague, complex, or involves multiple concepts. 
            This tool will write multiple versions of the user's query and search the vector database for relevant passages. 
            Returns a list of relevant passages."""
            
            llm = ChatOpenAI(model="gpt-4o-mini", temperature=0.5)
            retriever_from_llm = MultiQueryRetriever.from_llm(retriever=self.vectorstore.as_retriever(), llm=llm)
            documents = retriever_from_llm.invoke(query)
            return documents
        
        
        self.tools.append(vector_search)
        self.tools.append(multiple_query_vector_search)

In [37]:
# class ChatbotState(TypedDict):
#     # Messages have the type "list". The `add_messages` function defines how this state key should be updated
#     # (in this case, it appends messages to the list, rather than overwriting them)
#     messages: Annotated[list, add_messages]


class SRFChatbot:
    def __init__(
        self,
        chatbot_instructions: str,
        model: str = 'gpt-4o-mini',
        temperature: float = 0,
    ):
        # Initialize the LLM and the system message
        self.llm = ChatOpenAI(model=model, temperature=temperature)
        self.system_message = SystemMessage(content=chatbot_instructions)
        self.tools = ToolManager().get_tools()
        self.llm_with_tools = self.llm.bind_tools(self.tools)

        # Build the graph
        self.graph = self.build_graph()
        # Get the configurable
        self.config = self.get_configurable()
    

    def get_configurable(self):
        self.thread_id = str(uuid.uuid4())
        return {"configurable": {"thread_id": self.thread_id}}
        
    # Add the system message onto the llm
    def chatbot(self, state: MessagesState):
        messages = [self.system_message] + state["messages"]
        return {"messages": [self.llm_with_tools.invoke(messages)]}
    
    def build_graph(self):

        # Add chatbot state
        graph_builder = StateGraph(MessagesState)

        # Add nodes
        tool_node = ToolNode(self.tools)
        graph_builder.add_node("tools", tool_node)
        graph_builder.add_node("chatbot", self.chatbot)

        # Add a conditional edge wherein the chatbot can decide whether or not to go to the tools
        graph_builder.add_conditional_edges(
            "chatbot",
            tools_condition,
        )

        # Add fixed edges
        graph_builder.add_edge(START, "chatbot")
        graph_builder.add_edge("tools", "chatbot")

        # Instantiate the memory saver
        memory = MemorySaver()

        # Compile the graph
        return graph_builder.compile(checkpointer=memory)






In [59]:
chatbot_instructions = sp.system_prompt_templates['Open-Ended Bot']
chatbot = SRFChatbot(chatbot_instructions=chatbot_instructions)


In [61]:
query = "I am having a lot of trouble sleeping. What can I do?"
results = chatbot.graph.invoke({"messages": [HumanMessage(content=query)]}, chatbot.config)

In [62]:
chatbot.graph.get_state(chatbot.config).values['messages']

[HumanMessage(content='I am having a lot of trouble sleeping. What can I do?', additional_kwargs={}, response_metadata={}, id='49aec330-967f-48ec-a14c-3e2f351281b1'),
 AIMessage(content='', additional_kwargs={'tool_calls': [{'id': 'call_9mRC9uFfiJ3E7F1wmYuR7fSS', 'function': {'arguments': '{"query":"trouble sleeping"}', 'name': 'vector_search'}, 'type': 'function'}], 'refusal': None}, response_metadata={'token_usage': {'completion_tokens': 16, 'prompt_tokens': 249, 'total_tokens': 265, 'completion_tokens_details': {'reasoning_tokens': 0}}, 'model_name': 'gpt-4o-mini-2024-07-18', 'system_fingerprint': 'fp_e9627b5346', 'finish_reason': 'tool_calls', 'logprobs': None}, id='run-868473e1-e6e9-49be-9c87-973a9c9289dd-0', tool_calls=[{'name': 'vector_search', 'args': {'query': 'trouble sleeping'}, 'id': 'call_9mRC9uFfiJ3E7F1wmYuR7fSS', 'type': 'tool_call'}], usage_metadata={'input_tokens': 249, 'output_tokens': 16, 'total_tokens': 265}),
 ToolMessage(content="[Document(metadata={'chapter_name'

In [63]:
print(results['messages'][-1].content)

If you're having trouble sleeping, here are some insights from the teachings of Paramhansa Yogananda that may help:

1. **Understanding Sleep**: Sleep is described as an unconscious way of turning off life energy from the nerves. While you get some rest during sleep, it does not provide the conscious experience of bliss that meditation can offer. By practicing meditation and striving to reach a superconscious state, you can experience lasting spiritual changes and a deeper sense of joy that can accompany you even during your waking hours.

2. **Conscious Withdrawal**: Yogananda explains that the yogi learns to consciously withdraw from sensory nerves, allowing for a peaceful state of meditation. This practice can help you manage disturbances that might affect your sleep. By training yourself to switch off the senses at will, you can go beyond mere subconscious slumber into a blissful state of interiorization.

3. **The Nature of Sleep**: Sleep serves as a reminder of the soul's existen

In [66]:
def respond(message, history):
    # Format the history and new message into the expected structure
    formatted_messages = []
    for human, ai in history:
        formatted_messages.append(HumanMessage(content=human))
        if ai:  # AI might not have responded yet
            formatted_messages.append(AIMessage(content=ai))
    
    # Add the new message
    formatted_messages.append(HumanMessage(content=message))
    
    # Invoke the graph with properly formatted input
    result = chatbot.graph.invoke({"messages": formatted_messages}, chatbot.config)
    
    # Extract the assistant's response
    response = result["messages"][-1].content
    
    return response

# Create and launch the Gradio interface
gradio = gr.ChatInterface(respond)
gradio.launch(share=True)

Running on local URL:  http://127.0.0.1:7866
Running on public URL: https://94b754ba708e7402d2.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from Terminal to deploy to Spaces (https://huggingface.co/spaces)


In [74]:
import gradio as gr

# Get the prompt templates
prompt_templates = sp.system_prompt_templates

# Global variable to hold the current SRFChatbot instance
chatbot = SRFChatbot(chatbot_instructions=prompt_templates['Open-Ended Bot'])

def initialize_chatbot(prompt_name):
    selected_prompt = prompt_templates[prompt_name]
    chatbot = SRFChatbot(chatbot_instructions=selected_prompt)
    return selected_prompt, []  # Return the prompt text and reset the chat history

def chatbot_conversation(chat_history, user_query):
    global chatbot
    if chatbot is None:
        # Initialize with default prompt if not already initialized
        default_prompt = list(prompt_templates.keys())[0]
        chatbot = SRFChatbot(chatbot_instructions=prompt_templates[default_prompt])
    
    
    # Process the conversation
    result = respond(user_query, history)
    
    # Extract the bot's response
    bot_response = result["messages"][-1].content
    
    # Update the chat history
    chat_history.append((user_query, bot_response))
    
    return chat_history, ""

# Gradio interface
with gr.Blocks() as demo:
    gr.Markdown("# SRF Chatbot")
    
    with gr.Row():
        with gr.Column(scale=4):
            chatbot_output = gr.Chatbot()
            user_input = gr.Textbox(placeholder="Type your message here...")
            submit_button = gr.Button("Submit")
        
        with gr.Column(scale=1):
            system_prompt_dropdown = gr.Dropdown(
                choices=list(prompt_templates.keys()),
                label="Select System Prompt",
                value=list(prompt_templates.keys())[0]
            )
            system_prompt_display = gr.Textbox(
                value=prompt_templates[list(prompt_templates.keys())[0]],
                label="Current System Prompt",
                lines=5,
                interactive=False
            )
    
    system_prompt_dropdown.change(
        fn=initialize_chatbot,
        inputs=[system_prompt_dropdown],
        outputs=[system_prompt_display]
    )
    
    submit_button.click(
        fn=chatbot_conversation,
        inputs=[chatbot_output, user_input],
        outputs=[chatbot_output]
    )

# Initialize the chatbot with the default prompt
initialize_chatbot(list(prompt_templates.keys())[0])

demo.launch()

Running on local URL:  http://127.0.0.1:7869

To create a public link, set `share=True` in `launch()`.


Traceback (most recent call last):
  File "/Users/nadaa/.local/share/virtualenvs/srf_chatbot_v2-9vTIDuJW/lib/python3.11/site-packages/gradio/queueing.py", line 536, in process_events
    response = await route_utils.call_process_api(
               ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/Users/nadaa/.local/share/virtualenvs/srf_chatbot_v2-9vTIDuJW/lib/python3.11/site-packages/gradio/route_utils.py", line 322, in call_process_api
    output = await app.get_blocks().process_api(
             ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/Users/nadaa/.local/share/virtualenvs/srf_chatbot_v2-9vTIDuJW/lib/python3.11/site-packages/gradio/blocks.py", line 1935, in process_api
    result = await self.call_function(
             ^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/Users/nadaa/.local/share/virtualenvs/srf_chatbot_v2-9vTIDuJW/lib/python3.11/site-packages/gradio/blocks.py", line 1520, in call_function
    prediction = await anyio.to_thread.run_sync(  # type: ignore
                 ^^^^^^^^^^^^^^